In this notebook, I will experiment with a simple backtesting strategy using the `backtesting.py` library. The strategy will be tested on Bitcoin/USD 1-hour interval data. This workflow will demonstrate how to set up, implement, and evaluate a trading strategy using historical data.


In [ ]:
import os
import sys
# Add src folder to Python path
root_path = os.path.abspath(os.path.join(os.getcwd(), ".."))
print(f"Root path: {root_path}")
src_path = os.path.join(root_path, "src")
sys.path.append(src_path)

Root path: /Users/ezequielmrivero/git_projects/algo_repos/Crypto-Backtester-Duel
Src path: /Users/ezequielmrivero/git_projects/algo_repos/Crypto-Backtester-Duel/src


## Load data

In [13]:
from data.data_pipeline import get_historical_data
from utils.utils import polars_to_pandas
from config.config import CONFIG

In [15]:
df = get_historical_data(download=False)
df.head()

shape: (5, 12)
┌──────────────┬──────────┬──────────┬──────────┬───┬────────┬──────────────┬─────────────┬────────┐
│ open_time    ┆ open     ┆ high     ┆ low      ┆ … ┆ trades ┆ taker_base_v ┆ taker_quote ┆ ignore │
│ ---          ┆ ---      ┆ ---      ┆ ---      ┆   ┆ ---    ┆ ol           ┆ _vol        ┆ ---    │
│ datetime[ms] ┆ f64      ┆ f64      ┆ f64      ┆   ┆ i64    ┆ ---          ┆ ---         ┆ str    │
│              ┆          ┆          ┆          ┆   ┆        ┆ f64          ┆ f64         ┆        │
╞══════════════╪══════════╪══════════╪══════════╪═══╪════════╪══════════════╪═════════════╪════════╡
│ 2024-04-18   ┆ 61640.06 ┆ 61814.61 ┆ 60992.0  ┆ … ┆ 77973  ┆ 599.7186     ┆ 3.6867e7    ┆ 0      │
│ 05:00:00     ┆          ┆          ┆          ┆   ┆        ┆              ┆             ┆        │
│ 2024-04-18   ┆ 61072.02 ┆ 61320.0  ┆ 60803.35 ┆ … ┆ 81257  ┆ 770.62228    ┆ 4.7076e7    ┆ 0      │
│ 06:00:00     ┆          ┆          ┆          ┆   ┆        ┆              ┆             ┆        │
│ 2024-04-18   ┆ 61147.82 ┆ 61362.32 ┆ 60941.17 ┆ … ┆ 66304  ┆ 515.99398    ┆ 3.1564e7    ┆ 0      │
│ 07:00:00     ┆          ┆          ┆          ┆   ┆        ┆              ┆             ┆        │
│ 2024-04-18   ┆ 61178.08 ┆ 61550.0  ┆ 60864.0  ┆ … ┆ 74694  ┆ 814.83913    ┆ 4.9880e7    ┆ 0      │
│ 08:00:00     ┆          ┆          ┆          ┆   ┆        ┆              ┆             ┆        │
│ 2024-04-18   ┆ 61335.99 ┆ 61710.14 ┆ 61320.34 ┆ … ┆ 79267  ┆ 653.76921    ┆ 4.0216e7    ┆ 0      │
│ 09:00:00     ┆          ┆          ┆          ┆   ┆        ┆              ┆             ┆        │
└──────────────┴──────────┴──────────┴──────────┴───┴────────┴──────────────┴─────────────┴────────┘

## Defining strategy

In [ ]:
from backtesting import Strategy
from backtesting.lib import crossover
from backtesting.test import SMA
from backtesting import Backtest

class SmaCross_bt(Strategy):
    """
    A simple SMA Cross strategy:
    - If short SMA crosses above long SMA, enter a long position.
    - If short SMA crosses below long SMA, close the position.
    """

    n_short = 30
    n_long = 100

    def init(self):
        # Convert the series to indicators used by backtesting.py
        price = self.data.Close
        self.sma_short = self.I(SMA, price, self.n_short)
        self.sma_long = self.I(SMA, price, self.n_long)

    def next(self):
        # If short SMA crosses above long SMA, and not already in a trade:
        if crossover(self.sma_short, self.sma_long):
            self.buy()

        # If short SMA crosses below long SMA, close any open position:
        elif crossover(self.sma_long, self.sma_short):
            self.position.close()

In [44]:
def run_bt_sma_backtest(df_pl) -> None:
    df_pd = polars_to_pandas(df_pl)
    bt = Backtest(df_pd, SmaCross_bt, cash=1_000_000, commission=0.002, exclusive_orders=True)
    stats = bt.run()
    return stats, bt

stats, bt = run_bt_sma_backtest(df)
print(stats)
bt.plot()

Start                     2024-04-18 05:00:00
End                       2025-04-18 04:00:00
Duration                    364 days 23:00:00
Exposure Time [%]                    49.62329
Equity Final [$]                 924816.48874
Equity Peak [$]                 1421908.84716
Commissions [$]                  181543.90126
Return [%]                           -7.51835
Buy & Hold Return [%]                28.17156
Return (Ann.) [%]                     -7.4986
Volatility (Ann.) [%]                31.52198
CAGR [%]                             -7.51918
Sharpe Ratio                         -0.23788
Sortino Ratio                        -0.34974
Calmar Ratio                         -0.19802
Alpha [%]                           -19.69153
Beta                                  0.43211
Max. Drawdown [%]                   -37.86821
Avg. Drawdown [%]                    -3.21582
Max. Drawdown Duration      146 days 07:00:00
Avg. Drawdown Duration        9 days 23:00:00
# Trades                          

GridPlot(id='p4713', ...)

In [46]:
import optuna
from backtesting import Backtest

# Objective function for Optuna
def multi_objective(trial):
    # 1) Suggest parameters
    n_short = trial.suggest_int('n_short', 5, 50)
    # ensure n_long > n_short
    n_long  = trial.suggest_int('n_long', n_short + 1, 200)

    # 2) Update strategy class vars
    SmaCross_bt.n_short = n_short
    SmaCross_bt.n_long  = n_long

    # 3) Run backtest
    stats, _ = run_bt_sma_backtest(df)

    # 4) Extract objectives
    ret    = stats['Return [%]']    # e.g. 12.34
    sharpe = stats['Sharpe Ratio']  # e.g. 1.23

    # Optuna multi-objective: return a tuple
    return ret, sharpe

# Create a multi-objective study: maximize both return and sharpe
study = optuna.create_study(
    directions=['maximize', 'maximize'],
    study_name='sma_cross_multiobj'
)

# Run optimization
study.optimize(multi_objective, n_trials=300)
print("Number of Pareto-optimal trials:", len(study.best_trials))
for t in study.best_trials:
    print(f"  trial#{t.number}: Return={t.values[0]:.2f}%, Sharpe={t.values[1]:.2f}, "
          f"n_short={t.params['n_short']}, n_long={t.params['n_long']}")

[I 2025-04-20 20:52:31,756] A new study created in memory with name: sma_cross_multiobj
[I 2025-04-20 20:52:31,820] Trial 0 finished with values: [24.061439525999965, 0.5005459410938015] and parameters: {'n_short': 46, 'n_long': 79}.
[I 2025-04-20 20:52:31,868] Trial 1 finished with values: [-12.527045651999929, -0.3967908688536699] and parameters: {'n_short': 31, 'n_long': 49}.
[I 2025-04-20 20:52:31,912] Trial 2 finished with values: [3.93746675199999, 0.10340992837745012] and parameters: {'n_short': 22, 'n_long': 95}.
[I 2025-04-20 20:52:31,954] Trial 3 finished with values: [-4.452697692000016, -0.13336861429880492] and parameters: {'n_short': 40, 'n_long': 144}.
[I 2025-04-20 20:52:31,996] Trial 4 finished with values: [-12.230213979999977, -0.40284929431355837] and parameters: {'n_short': 33, 'n_long': 151}.
[I 2025-04-20 20:52:32,038] Trial 5 finished with values: [15.411267801999953, 0.3720265747027527] and parameters: {'n_short': 39, 'n_long': 121}.
[I 2025-04-20 20:52:32,080]

Number of Pareto-optimal trials: 1
  trial#241: Return=54.64%, Sharpe=0.93, n_short=47, n_long=67


In [56]:
import optuna
from backtesting import Backtest

# Objective function for Optuna
def single_objective(trial):
    # 1) Suggest parameters
    n_short = trial.suggest_int('n_short', 5, 50)
    # ensure n_long > n_short
    n_long  = trial.suggest_int('n_long', n_short + 1, 200)

    # 2) Update strategy class vars
    SmaCross_bt.n_short = n_short
    SmaCross_bt.n_long  = n_long

    # 3) Run backtest
    stats, _ = run_bt_sma_backtest(df)

    # 4) Extract objectives
    ret    = stats['Return [%]']    # e.g. 12.34
    sharpe = stats['Sharpe Ratio']  # e.g. 1.23

    return ret + 10*sharpe

# Create a multi-objective study: maximize both return and sharpe
study = optuna.create_study(
    direction='maximize',
    study_name='sma_cross_singleobj'
)

# Run optimization
study.optimize(single_objective, n_trials=300)
print("Number of Pareto-optimal trials:", len(study.best_trials))
for t in study.best_trials:
    print(f"  trial#{t.number}: "
          f"n_short={t.params['n_short']}, n_long={t.params['n_long']}")

[I 2025-04-20 20:59:22,646] A new study created in memory with name: sma_cross_singleobj
[I 2025-04-20 20:59:22,711] Trial 0 finished with value: 8.24956546619322 and parameters: {'n_short': 41, 'n_long': 100}. Best is trial 0 with value: 8.24956546619322.
[I 2025-04-20 20:59:22,759] Trial 1 finished with value: -75.55388818135232 and parameters: {'n_short': 11, 'n_long': 21}. Best is trial 0 with value: 8.24956546619322.
[I 2025-04-20 20:59:22,802] Trial 2 finished with value: -54.7639386556591 and parameters: {'n_short': 20, 'n_long': 54}. Best is trial 0 with value: 8.24956546619322.
[I 2025-04-20 20:59:22,847] Trial 3 finished with value: -38.35449866371697 and parameters: {'n_short': 6, 'n_long': 55}. Best is trial 0 with value: 8.24956546619322.
[I 2025-04-20 20:59:22,889] Trial 4 finished with value: -37.63886359621456 and parameters: {'n_short': 22, 'n_long': 55}. Best is trial 0 with value: 8.24956546619322.
[I 2025-04-20 20:59:22,932] Trial 5 finished with value: 5.1968573586

Number of Pareto-optimal trials: 2
  trial#161: n_short=42, n_long=106
  trial#205: n_short=42, n_long=106


In [57]:
SmaCross_bt.n_short = 47
SmaCross_bt.n_long  = 67
stats, bt = run_bt_sma_backtest(df)
print(stats)
bt.plot()

Start                     2024-04-18 05:00:00
End                       2025-04-18 04:00:00
Duration                    364 days 23:00:00
Exposure Time [%]                    50.99315
Equity Final [$]                1546408.47854
Equity Peak [$]                 1977205.05482
Commissions [$]                  406159.29146
Return [%]                           54.64085
Buy & Hold Return [%]                30.37102
Return (Ann.) [%]                    54.45677
Volatility (Ann.) [%]                58.25963
CAGR [%]                             54.64854
Sharpe Ratio                          0.93473
Sortino Ratio                         2.69825
Calmar Ratio                          1.93195
Alpha [%]                            40.74698
Beta                                  0.45747
Max. Drawdown [%]                   -28.18741
Avg. Drawdown [%]                    -1.75589
Max. Drawdown Duration      121 days 14:00:00
Avg. Drawdown Duration        4 days 01:00:00
# Trades                          

GridPlot(id='p5463', ...)

In [58]:
SmaCross_bt.n_short = 42
SmaCross_bt.n_long  = 106
stats, bt = run_bt_sma_backtest(df)
print(stats)
bt.plot()

Start                     2024-04-18 05:00:00
End                       2025-04-18 04:00:00
Duration                    364 days 23:00:00
Exposure Time [%]                    50.97032
Equity Final [$]                1317633.81928
Equity Peak [$]                  1824233.4659
Commissions [$]                  218347.08072
Return [%]                           31.76338
Buy & Hold Return [%]                28.21663
Return (Ann.) [%]                    31.66412
Volatility (Ann.) [%]                47.72697
CAGR [%]                             31.76753
Sharpe Ratio                          0.66344
Sortino Ratio                         1.51527
Calmar Ratio                          0.96982
Alpha [%]                            19.37035
Beta                                  0.43921
Max. Drawdown [%]                   -32.64957
Avg. Drawdown [%]                    -2.26621
Max. Drawdown Duration      121 days 14:00:00
Avg. Drawdown Duration        4 days 15:00:00
# Trades                          

GridPlot(id='p5839', ...)